<a href="https://colab.research.google.com/github/raveinnovate/DATA304-Project/blob/main/md_schools-map_w_bmore_emphasis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Maryland K-12 Schools - Map Visualization

## Mount Drive (Colab-Specific)

In [41]:
# Colab Specific cmd - mount drive/access data
from google.colab import drive
drive.mount('/content/drive')


%cd /content/drive/MyDrive/data304_childrens_program/


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/MyDrive/data304_childrens_program


## Import Statements

In [42]:
# Import Statements
import folium
import pandas as pd
import requests
import json
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
import plotly.express as px
import math
import branca
from folium import IFrame
from folium.features import Popup

## Access/Convert Maryland.gov API Data to Dataframe

In [43]:
# MD.GOV API URL
md_schools_url = "https://services.arcgis.com/njFNhDsUCentVYJW/arcgis/rest/services/Maryland_K_12_Schools/FeatureServer/0/query?where=1%3D1&outFields=*&outSR=4326&f=json"

md_schools_info = requests.get(md_schools_url)

# Convert response data to JSON
mds = md_schools_info.json()

# Create Dataframe from JSON
school_df = pd.DataFrame([feature['attributes'] for feature in mds['features']])

# Display Dataframe w/School Data
school_df

FID          county                                      school_nam  \
0        1  Baltimore City                       Wolfe Street Academy #023   
1        2  Baltimore City      Monarch Academy Public Charter School #381   
2        3  Baltimore City       Furman Templeton Preparatory Academy #125   
3        4  Baltimore City                     Hampstead Hill Academy #047   
4        5  Baltimore City          Rosemont Elementary/Middle School #063   
...    ...             ...                                             ...   
1424  1425  Baltimore City  Harriet Tubman Elementary School Building #138   
1425  1426      Montgomery                    Wells (Hallie) Middle School   
1426  1427      Washington                Jonathan Hager Elementary School   
1427  1428  Baltimore City     Baltimore Leadership School for Young Women   
1428  1429      Washington                          Public Service Academy   

                             address        city    zip                type  \
0             245 South Wolfe Street   Baltimore  21231             Charter   
1                   2525 Kirk Avenue   Baltimore  21218             Charter   
2     1200 North Pennsylvania Avenue   Baltimore  21217             Charter   
3           500 South Linwood Avenue   Baltimore  21224             Charter   
4              2777 Presstman Street   Baltimore  21216             Charter   
...                              ...         ...    ...                 ...   
1424              1807 Harlem Avenue   Baltimore      0   Public Elementary   
1425     11701 Little Seneca Parkway  Clarksburg      0       Public Middle   
1426              12615 Sedgwick Way  Hagerstown      0   Public Elementary   
1427        126 West Franklin Street   Baltimore      0  Public Middle/High   
1428            701 Frederick Street  Hagerstown      0              Public   

              grades   Format                              GlobalID  
0     Grades: PK - 5  Charter  78720bda-ed5a-42a1-aa4c-91e9a87801ba  
1      Grades: K - 8  Charter  494af5a1-5edd-4e99-ba26-6ca2558c94c4  
2     Grades: PK - 5  Charter  238ce3b7-346b-41a8-a0e0-cfc00df90e77  
3     Grades: PK - 8  Charter  e99610c6-bfa2-42da-818c-bcf2fd73348f  
4     Grades: PK - 8  Charter  8e90f1ed-64d3-4e88-abc1-663d0248f431  
...              ...      ...                                   ...  
1424             K-5   Public  1e7e86b4-9766-49b8-b72e-2212d29671ab  
1425             6-8   Public  1881bb28-5d05-4f24-b049-0025f7143c58  
1426          PreK-5   Public  aab4325e-5c4d-4a46-ae0e-d79c4f51c60e  
1427            6-12   Public  0086e67f-cc08-499e-9baa-e798bf25cfd1  
1428                   Public  1191e282-7750-4e59-a850-4a7ff395f5a0  

[1429 rows x 10 columns]

In [44]:
# Create coordinate dataframe (df)
coords_df = pd.DataFrame([feature['geometry'] for feature in mds['features']])

# Display coordinate df
coords_df

x          y
0    -76.589850  39.287999
1    -76.600217  39.318842
2    -76.630402  39.299712
3    -76.576293  39.285853
4    -76.663132  39.304482
...         ...        ...
1424 -76.646617  39.296005
1425 -77.239441  39.232380
1426 -77.758125  39.660419
1427 -76.618067  39.295290
1428 -77.716443  39.628686

[1429 rows x 2 columns]

## Clean Dataframes

In [45]:
# Clean column names for school_df
school_df = school_df.rename(columns=str.lower)
print(school_df.columns)

# Clean column names for coords_df
coords_df = coords_df.rename(columns=str.lower)

# Rename columns to longitude and latitude
coords_df.columns = ["long", "lat"]

# Combine 2 dataframes
combo_df = school_df
combo_df["lats"] = coords_df['lat']
combo_df["longs"] = coords_df['long']


Index(['fid', 'county', 'school_nam', 'address', 'city', 'zip', 'type',
       'grades', 'format', 'globalid'],
      dtype='object')


## Analyze Combined Dataframe for Insights

In [46]:
# Analyze combined df, combo_df
print("[ANALYZE DATAFRAME]\n\n")
print("GENERAL INFO ########################")
print(combo_df.info())
print("DESCRIBE ########################")
print(combo_df.describe())
print("\nCOLUMNS ########################")
print(combo_df.columns)
print("\nDF SHAPE ########################")
print(combo_df.shape)
print("\nDF DATATYPES ########################")
print(combo_df.dtypes)
print("\nDF LENGTH ########################")
print(len(combo_df))


[ANALYZE DATAFRAME]


GENERAL INFO ########################
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1429 entries, 0 to 1428
Data columns (total 12 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   fid         1429 non-null   int64  
 1   county      1429 non-null   object 
 2   school_nam  1429 non-null   object 
 3   address     1429 non-null   object 
 4   city        1429 non-null   object 
 5   zip         1429 non-null   int64  
 6   type        1429 non-null   object 
 7   grades      1429 non-null   object 
 8   format      1429 non-null   object 
 9   globalid    1429 non-null   object 
 10  lats        1429 non-null   float64
 11  longs       1429 non-null   float64
dtypes: float64(2), int64(2), object(8)
memory usage: 134.1+ KB
None
DESCRIBE ########################
              fid           zip         lats        longs
count  1429.00000   1429.000000  1429.000000  1429.000000
mean    715.00000  16929.675297    39.13

In [89]:
# Load Baltimore Zipcode Data from Open Baltimore
# Open Baltimore (.gov)
# https://data.baltimorecity.gov

with open('data/zipcodes.json', 'r') as file:
    zip = json.load(file)

# Baltimore, MD coordinates
center_lat = 39.2904
center_lon = -76.6122
mile_radius = 3

# 1 degree latitude ≈ 69 miles
lat_offset = mile_radius / 69

# 1 degree longitude ≈ 69 * cos(latitude) miles
lon_offset = mile_radius / (69 * math.cos(math.radians(center_lat)))

# Compute bounds
min_lat = center_lat - lat_offset
max_lat = center_lat + lat_offset
min_lon = center_lon - lon_offset
max_lon = center_lon + lon_offset

# Create base map
m = folium.Map(
    max_bounds=True,
    location=[39.2904, -76.6122],
    zoom_start=14,
    min_lat=min_lat,
    max_lat=max_lat,
    min_lon=min_lon,
    max_lon=max_lon,
)

folium.CircleMarker([max_lat, min_lon], tooltip="Upper Left Corner").add_to(m)
folium.CircleMarker([min_lat, min_lon], tooltip="Lower Left Corner").add_to(m)
folium.CircleMarker([min_lat, max_lon], tooltip="Lower Right Corner").add_to(m)
folium.CircleMarker([max_lat, max_lon], tooltip="Upper Right Corner").add_to(m)


# Add Baltimore Zip Codes data to map
folium.GeoJson(zip).add_to(m)

# Add associated zipcode name and zipcode as pop on map for each zipcode
popup = folium.GeoJsonPopup(fields=["zipname", "zipcode1"])

# Highlight Paul's Place zipcodes of interest in the color dark purple
# All 3 service schools are located in either 21230 or 21223 zipcodes
folium.GeoJson(
    zip,
    highlight_function=lambda feature: {
        "color": "purple",
        "fillColor": (
            "darkpurple" if "21230" in feature["properties"]["zipcode1"].lower() else "white"
            "darkpurple" if "21223" in feature["properties"]["zipcode1"].lower() else "white"
        ),
    },
    popup=popup,
    popup_keep_highlighted=True,
).add_to(m)

html = """
    <h1> Paul's Place - Baltimore MD</h1><br>
    <a href="https://paulsplaceoutreach.org/"><h2>Link to Site</h2></a>

"""

folium.Marker([39.2820, -76.6329], icon=folium.Icon(icon='map-pin', prefix='fa', color="green"), popup=html, ).add_to(m)



# Add Paul's Place Schools to Map
for lat, long, name in combo_df[["lats", "longs", "school_nam"]].values:
  school_html = f"""
    <h1>{name}</h1><br>
    <h1>{lat},{long}</h1><br>
    <a href=""><h2>Link to Site</h2></a>

  """
  folium.Marker([lat, long], icon=folium.Icon(icon='school', prefix='fa', color='purple'),popup=school_html).add_to(m)

m

## Maryland Schools and Zip Codes

In [83]:
# show map
m